# Ideal Lockdown Location

#### Assessing Dublin areas for the ideal place to live during a 5km lockdown compared to pre-lockdown
#### A project completed as part of the IBM Data Science Professional Certificate

### Table of Contents

* [Introduction: Business Problem](#business-problem)
* [Data](#data)
* [Methodology](#methodology)
* [Results](#results)
* [Discussion](#discussion)
* [Conclusion](#conclusion)
* [Reference](#reference)

### Introduction <a class="anchor" id="business-problem"></a>

In this project we are going to look for the optimal location in which to live, taking into account the amenities available within a 5km radius, the average rent, and the latest Covid-19 incidence rate. Specifically, this report will focus on Dublin, Ireland during the Covid-19 pandemic.

As of April 2021, over the past year residents of Ireland have been been required to stay within 5kms of their home for a total of 7 months, off and on. During this time, the vast majority of amenities were closed, with only supermarkets, pharmacies and other essential services open for business. As such, neighbourhoods that were previously very in demand due to their proximity to amenities, such as in the city centre, no longer held as much of an appeal. Indeed, with so much of the population working from home, the focus seems to have shifted from having shorter commuting times to having recreational spaces nearby.

As a result, many residents of Dublin have been tempted to move out of the city to areas with cheaper rent and more or comparable available amenities. This project aims to help them identify where they should consider moving to.

Dublin is the capital of Ireland and includes both the city and the surrounding suburbs and townlands. In this report, we will investigate all areas of Dublin to determine their desirability pre-Covid and during the pandemic. We will first divide the county up and then assess each area, before comparing them and drawing conclusions about the ideal place to live.

### Data <a class="anchor" id="data"></a>

Based on the definition of our problem, factors that may impact our decision are:

- The number of amenities within a 5km radius
- The number of amenities within a 5km radius that are open during Level 5 lockdown
- The average rent in the area
- The latest 14-Day Incidence Rate in the area
   
We decided to use a regularly spaced grid of centroids across Dublin to define our neighborhoods.

In this project, we will fetch or extract data from the following data sources:

- Amenities in each neighborhood will be obtained using Foursquare API
- Average monthly rent will be obtained from Ireland's [Central Statistics Office](https://data.cso.ie/)
- Dublin shapefile is obtained from [data.gov.ie](https://data.gov.ie/dataset/counties-osi-national-statutory-boundaries1), Ireland's open data portal
- Dublin Local Electoral Areas and 14-Day Covid-19 incidence rate per 100,000 is sourced from [Covid-19 GeoHive](https://covid-19.geohive.ie/datasets/27d401c9ae084097bb1f3a69b69462a1_0), Ireland's Covid-19 Hub
- Centers of the neighborhoods will be generated algorithmically and approximate addresses of centers of those areas will be obtained using Nominatim
- Coordinate of Dublin center will be obtained using Nominatim

Imports

In [1]:
#!pip install folium
#!pip install shapely
#!pip install colour

In [2]:
import numpy as np
import pandas as pd
import folium
from geopy.geocoders import Nominatim
import requests
import json
import math
from shapely.geometry import shape, Point, Polygon
from colour import Color

In [3]:
# The code was removed by Watson Studio for sharing.

Your credentails:
CLIENT_ID: JL43APTRB5BUAZPTEJKDXW52LOW54VR0NQCV3JHEB3K1E5GX
CLIENT_SECRET:PFY0EJVYPG00NPH4XJCI2BOLJDO3QSJLH04LLHM1YTLV1JOY


#### A map of Dublin

In [4]:
address = 'Dublin, Ireland'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Dublin are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Dublin are 53.3497645, -6.2602732.


In [5]:
figure_dublin = folium.Figure(width=500, height=600)
folium.Map(location=[latitude, longitude], zoom_start=11).add_to(figure_dublin)
    
figure_dublin

#### Load Dublin Shapefile

In [6]:
# The code was removed by Watson Studio for sharing.

In [7]:
file = project.get_file('Dublin.geojson')

In [8]:
geojson_text = file.read()
geojson = json.loads(geojson_text)

In [9]:
def read_geojson(filepath):
    with open(filepath, 'r') as f:
        js = json.load(f)
    return js

def get_boundary_from_geojson(geojson):
    js = read_geojson(geojson) if isinstance(geojson, str) else geojson
    return shape(geojson['features'][0]['geometry']).bounds

def is_in_geojson(geojson, point):    
    js = read_geojson(geojson) if isinstance(geojson, str) else geojson
    pos = point if isinstance(point, Point) else Point(point)

    for feature in js['features']:
        polygon = shape(feature['geometry'])
        if polygon.contains(pos):
            return True
    return False

In [10]:
boundary = get_boundary_from_geojson(geojson)
print(f'The boundaries of Dublin: {boundary}\n')

dublin_centre_lon = (boundary[0] + boundary[2]) /2
dublin_centre_lat = (boundary[1] + boundary[3]) /2
print(f'The centre of Dublin is {dublin_centre_lon}, {dublin_centre_lat}')

The boundaries of Dublin: (-6.54688533611748, 53.1781973864789, -5.99627779996316, 53.6347253423409)

The centre of Dublin is -6.27158156804032, 53.4064613644099


In [11]:
figure_dublin = folium.Figure(width=500, height=600)
map_dublin = folium.Map(location=(dublin_centre_lat, dublin_centre_lon), zoom_start=10).add_to(figure_dublin)
folium.GeoJson(geojson).add_to(map_dublin)
figure_dublin

#### Generate 1km spaced points on map

In [12]:
r_earth = 6378

In [13]:
def get_next_lat(lat, y):
    new_lat = lat + (y / r_earth) * (180 / math.pi);
    return new_lat
    
def get_next_lon(lon, lat, x):
    new_lon = lon + (x / r_earth) * (180 / math.pi) / math.cos(lat * math.pi/180);
    return new_lon

In [14]:
step = 1000

latitudes = []
longitudes = []

lat = boundary[1]
while lat < boundary[3]:
    lon = boundary[0]
    while lon < boundary[2]:
        if is_in_geojson(geojson, (lon, lat)):
            latitudes.append(lat)
            longitudes.append(lon)
        lon = get_next_lon(lon, lat, 1)
    lat = get_next_lat(lat, 1)

In [15]:
zipped_lat_lon = zip(latitudes, longitudes)

figure_dublin = folium.Figure(width=500, height=600)
map_dublin = folium.Map(location=(dublin_centre_lat, dublin_centre_lon), zoom_start=10).add_to(figure_dublin)
folium.GeoJson(geojson).add_to(map_dublin)

for latlon in zipped_lat_lon:
    folium.Circle(latlon).add_to(map_dublin)
figure_dublin

#### Import rent

In [16]:
# The code was removed by Watson Studio for sharing.

In [17]:
rent_df = rent_df.dropna()
rent_df = rent_df.rename(columns={"VALUE": "Avg Rent"}, errors="raise")

In [18]:
def get_lon_lat(location):
    loc = geolocator.geocode(location + ", Ireland")
    if(loc == None):
        return (np.NaN, np.NaN)
    return (loc.longitude, loc.latitude)

In [19]:
rent_df['Longitude'], rent_df['Latitude'] = zip(*rent_df.Location.apply(get_lon_lat))

In [20]:
rent_df = rent_df.dropna()

In [21]:
red_to_green = list(Color("red").range_to(Color("green"),11))
green_to_red = list(Color("green").range_to(Color("red"),11))

In [22]:
def GetColor(row, col, col_max, col_min, colours):
    curr = row[col]
    colour_index = (int)(((curr-col_min)/(col_max-col_min))*10)
    return colours[colour_index]

def GetColorScaled(scaled, colours):
    colour_index = (int)(scaled*10)
    return colours[colour_index]

In [23]:
zipped_lat_lon = zip(latitudes, longitudes)

figure_dublin = folium.Figure(width=300, height=400)
map_dublin = folium.Map(location=[latitude, longitude], tiles="cartodbpositron", zoom_start=10).add_to(figure_dublin)
col_max = rent_df["Avg Rent"].max()
col_min = rent_df["Avg Rent"].min()

for index, row in rent_df.iterrows():
    circle_color = GetColor(row, "Avg Rent", col_max, col_min, green_to_red)
    folium.Circle((row.Latitude, row.Longitude), color=circle_color.hex).add_to(map_dublin)

figure_dublin

#### Import latest Covid 14-Day Incidence Rate

In [24]:
leas_url = "https://opendata.arcgis.com/datasets/27d401c9ae084097bb1f3a69b69462a1_0.geojson?where=COUNTY%20%3D%20'DUBLIN'"

In [25]:
leas = requests.get(leas_url).json()

In [26]:
figure_dublin = folium.Figure(width=500, height=600)
map_dublin = folium.Map(location=(dublin_centre_lat, dublin_centre_lon), zoom_start=10).add_to(figure_dublin)
folium.GeoJson(leas).add_to(map_dublin)
figure_dublin

#### Get all category types for classification

In [27]:
categories_url = 'https://api.foursquare.com/v2/venues/categories?client_id={}&client_secret={}&v={}'.format(CLIENT_ID, CLIENT_SECRET, VERSION)
all_categories = requests.get(categories_url).json()

In [28]:
def get_top_categories(json):
    top_categories = pd.DataFrame()
    for entry in json:
        if 'id' in entry:
            new_row = {'id':entry['id'], 'name':entry['name']}
            top_categories = top_categories.append(new_row, ignore_index=True)
    return top_categories

In [29]:
def get_all_categories(category, category_list):
    if 'categories' in category:
        for sub in category['categories']:
            get_all_categories(sub, category_list)
    if 'id' in category:
        detail = category['id'] + ',' + category['name']
        category_list.append(detail)

In [30]:
category_list = []
get_all_categories((all_categories['response']), category_list)

In [31]:
top_categories = get_top_categories(all_categories['response']['categories'])

The category list was then classified by hand offline

#### Import classified categories

In [32]:
# The code was removed by Watson Studio for sharing.

Id           Name  QualityOfLife  Open  Delivery
0  56aa371be4b08b9a8d5734db   Amphitheater              1     0         0
1  4fceea171983d5d06c3e9823       Aquarium              1     0         0
2  4bf58dd8d48988d1e1931735         Arcade              1     0         0
3  4bf58dd8d48988d1e2931735    Art Gallery              1     0         0
4  4bf58dd8d48988d1e4931735  Bowling Alley              1     0         0

#### Test pulling data for one area

It was observed during testing with Clonsilla that if we simply sent one request for all venues within a 5km radius, many of them would be cut off due to the 100 results cap on the FourSquare API. This was particularly relevant for the lockdown analysis as many of the venues available during lockdown (smaller supermarkets, small parks etc) would have been excluded in favour of more popular venues such as restaurants and cinemas. As a result, it was decided that if there were more than 100 results from the first query, a series of subsequent queries would be sent for each of the major subcategories. This returned much more favourable results.

In [33]:
address = 'Clonsilla, Dublin'

clonsilla_location = geolocator.geocode(address)
clonsilla_latitude = clonsilla_location.latitude
clonsilla_longitude = clonsilla_location.longitude
print('The geograpical coordinate of Clonsilla are {}, {}.'.format(clonsilla_latitude, clonsilla_longitude))

The geograpical coordinate of Clonsilla are 53.383333, -6.416667.


In [34]:
radius = 5000
LIMIT = 1000
category = '4d4b7104d754a06370d81259'
full_url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&ll={},{}&v={}&radius={}&limit={}'.format(CLIENT_ID, CLIENT_SECRET, clonsilla_latitude, clonsilla_longitude, VERSION, radius, LIMIT)

In [35]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [36]:
result_df = pd.DataFrame()
total_results = requests.get(full_url).json()
if total_results['response']['totalResults'] > 100:
    for index, category in top_categories.iterrows():
        category_url = full_url + '&categoryId=' + (category['id'])
        category_results = requests.get(category_url).json()
        if category_results['response']['totalResults'] > 0:
            normalised = pd.json_normalize(category_results['response']['groups'][0]['items'])
            filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
            normalised = normalised.loc[:, filtered_columns]
            normalised['venue.categories'] = normalised.apply(get_category_type, axis=1)
            normalised.columns = [col.split(".")[-1] for col in normalised.columns]
            result_df = result_df.append(normalised)
else:
    normalised = pd.json_normalize(total_results['response']['groups'][0]['items'])
    filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
    normalised = normalised.loc[:, filtered_columns]
    normalised['venue.categories'] = normalised.apply(get_category_type, axis=1)
    normalised.columns = [col.split(".")[-1] for col in normalised.columns]
    result_df = result_df.append(normalised)

In [37]:
result_df = result_df.join(classified_categories.set_index('Name'), on='categories')

In [38]:
result_df['Neighborhood Longitude'] = clonsilla_longitude
result_df['Neighborhood Latitude'] = clonsilla_latitude

In [39]:
result_df.head()

name                 categories  \
0                                   Odeon                  Multiplex   
1                                Draíocht                    Theater   
2                                     Vue              Movie Theater   
0  Institute of Technology Blanchardstown                 University   
1                           LINC Building  College Academic Building   

         lat       lng                        Id  QualityOfLife  Open  \
0  53.392478 -6.391169  4bf58dd8d48988d180941735              1     0   
1  53.391233 -6.391376  4bf58dd8d48988d137941735              1     0   
2  53.352747 -6.393769  4bf58dd8d48988d17f941735              1     0   
0  53.405142 -6.378307  4bf58dd8d48988d1ae941735              1     0   
1  53.406518 -6.379751  4bf58dd8d48988d198941735              1     0   

   Delivery  Neighborhood Longitude  Neighborhood Latitude  
0         0               -6.416667              53.383333  
1         0               -6.416667              53.383333  
2         0               -6.416667              53.383333  
0         0               -6.416667              53.383333  
1         0               -6.416667              53.383333

In [40]:
print(f'Number of venues in Clonsilla: {len(result_df)}');
print(f'Clonsilla venues open during Level 5 lockdown: {len(result_df[result_df.Open == 1])}')

Number of venues in Clonsilla: 337
Clonsilla venues open during Level 5 lockdown: 67


#### Get venues for all points

In [41]:
def getNearbyVenues(latitudes, longitudes, radius=5000):
    
    result_df = pd.DataFrame()
    for lat, lng in zip(latitudes, longitudes):
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            1000)
            
        try:
            total_results = requests.get(url).json()
            if total_results['response']['totalResults'] > 100:
                for index, category in top_categories.iterrows():
                    try:
                        category_url = url + '&categoryId=' + (category['id'])
                        category_results = requests.get(category_url).json()
                        if category_results['response']['totalResults'] > 0:
                            normalised = pd.json_normalize(category_results['response']['groups'][0]['items'])
                            filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
                            normalised = normalised.loc[:, filtered_columns]
                            normalised['venue.categories'] = normalised.apply(get_category_type, axis=1)
                            normalised.columns = [col.split(".")[-1] for col in normalised.columns]
                            normalised['Neighborhood Longitude'] = lng
                            normalised['Neighborhood Latitude'] = lat
                            result_df = result_df.append(normalised)
                    except:
                      print("Error retrieving with url", category_url)
            else:
                normalised = pd.json_normalize(total_results['response']['groups'][0]['items'])
                filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
                normalised = normalised.loc[:, filtered_columns]
                normalised['venue.categories'] = normalised.apply(get_category_type, axis=1)
                normalised.columns = [col.split(".")[-1] for col in normalised.columns]
                normalised['Neighborhood Longitude'] = lng
                normalised['Neighborhood Latitude'] = lat
                result_df = result_df.append(normalised)
        except:
          print("Error retrieving with url", url)
    
    return(result_df)

In [ ]:
dublin_venues = getNearbyVenues(latitudes, longitudes)

### Methodology <a class="anchor" id="methodology"></a>

#### Amalgamate into one dataset

First the data needed to amalgamated into one dataset, with one row for each neighborhood.

Add category classification to retrieved venues by joining on category type

In [ ]:
dublin_venues = dublin_venues.join(classified_categories.set_index('Name'), on='categories')

In [ ]:
dublin_venues = dublin_venues[dublin_venues.QualityOfLife == 1]

Group venues into neighborhoods, summing the number of each type of amenity

In [ ]:
neighborhoods = dublin_venues.groupby(['Neighborhood Latitude', 'Neighborhood Longitude']).agg({"QualityOfLife": "sum", "Open": "sum", "Delivery":"sum"})

In [ ]:
neighborhoods = neighborhoods.reset_index()

In [ ]:
neighborhoods.head()

Add rental data by determining the nearest data point from the available rent data

In [ ]:
zipped_lat_lon = zip(latitudes, longitudes)

figure_dublin = folium.Figure(width=300, height=400)
map_dublin = folium.Map(location=[latitude, longitude], tiles="cartodbpositron", zoom_start=9).add_to(figure_dublin)
col_max = rent_df["Avg Rent"].max()
col_min = rent_df["Avg Rent"].min()

for index, row in rent_df.iterrows():
    circle_color = GetColor(row, "Avg Rent", col_max, col_min, green_to_red)
    folium.Circle((row.Latitude, row.Longitude), color=circle_color.hex).add_to(map_dublin)

figure_dublin

In [ ]:
def get_nearest_price(lat, lon):
    shortest_dist = 1000
    shortest_index = 0
    for index, row in rent_df.iterrows():
        dist = math.sqrt(math.pow(row.Latitude - lat, 2) + math.pow(row.Longitude - lon, 2))
        if(dist < shortest_dist):
            shortest_dist = dist
            shortest_index = index
    return rent_df.at[shortest_index, 'Avg Rent']

In [ ]:
neighborhoods['Avg Rent'] = neighborhoods.apply(lambda x: get_nearest_price(x['Neighborhood Latitude'], x['Neighborhood Longitude']), axis=1)

In [ ]:
neighborhoods.head()

Add Covid-19 incidence by determining that of the containing Local Electoral Area

In [ ]:
def get_covid_cases(geojson, point):
    pos = Point(point)

    for feature in geojson['features']:
        polygon = shape(feature['geometry'])
        if polygon.contains(pos):
            return feature['properties']["P14_100k"]
    return False

In [ ]:
neighborhoods['CovidCasesPer100000'] = neighborhoods.apply(lambda x: get_covid_cases(leas, (x['Neighborhood Longitude'], x['Neighborhood Latitude'])), axis=1)

In [ ]:
neighborhoods.head()

#### Scale the data

Once we had the dataset in place, we needed to scale the data so it could be easily compared

In [ ]:
import pandas as pd
from sklearn import preprocessing

x = neighborhoods[['QualityOfLife', 'Open', 'Delivery', 'Avg Rent', 'CovidCasesPer100000']].values
min_max_scaler = preprocessing.MinMaxScaler()

x_scaled = min_max_scaler.fit_transform(x)
df = pd.DataFrame(x_scaled)
df.columns = ['QualityOfLife_Scaled', 'Open_Scaled', 'Delivery_Scaled', 'Avg Rent_Scaled', 'CovidCasesPer100000_Scaled']

In [ ]:
neighborhoods = pd.concat([neighborhoods, df], axis=1)

The data was then visualised to spot any issues

In [ ]:
def draw_map(title, color_col, name_col, high_is_good):
    print(title)
    figure_dublin = folium.Figure(width=300, height=400)

    map_dublin = folium.Map(location=(dublin_centre_lat, dublin_centre_lon), tiles="cartodbpositron", zoom_start=9).add_to(figure_dublin)
    folium.GeoJson(geojson).add_to(map_dublin)

    for index, row in neighborhoods.iterrows():
        color_scale = red_to_green if high_is_good else green_to_red
        circle_color = GetColorScaled(row[color_col], color_scale)
        folium.Circle((row["Neighborhood Latitude"], row["Neighborhood Longitude"]), color=circle_color.hex).add_child(folium.Popup('€' + (str)(row[name_col]))).add_to(map_dublin)

    return figure_dublin

In [ ]:
draw_map("Quality of Life", "QualityOfLife_Scaled", "QualityOfLife", True)

In [ ]:
draw_map("Open Amenities", "Open_Scaled", "Open", True)

In [ ]:
draw_map("Food Delivery Options", "Delivery_Scaled", "Delivery", True)

In [ ]:
draw_map("14-Day Incidence Rate per 100,000", "CovidCasesPer100000_Scaled", "CovidCasesPer100000", False)

In [ ]:
draw_map("Average Rent in Euro", "Avg Rent_Scaled", "Avg Rent", False)

The first four maps look like an appropriate spread, but the rent appears to be suffering from outliers. This can be confirmed with visualisation using a histogram.

In [ ]:
neighborhoods['Avg Rent'].plot(kind="hist")

The histogram is right skewed and so confirms the hypothesis

In [ ]:
x = neighborhoods[['Avg Rent']]
standard_scaler = preprocessing.QuantileTransformer()

x_scaled = standard_scaler.fit_transform(x)
df = pd.DataFrame(x_scaled)
df.columns = ['Avg Rent_Scaled']

In [ ]:
df['Avg Rent_Scaled'].plot(kind="hist")

In [ ]:
neighborhoods['Avg Rent_Scaled'] = df['Avg Rent_Scaled']

In [ ]:
draw_map("Average Rent in Euro", "Avg Rent_Scaled", "Avg Rent", False)

#### Add score using weighted sum

In order to compare the neighborhoods, each needed to be given a score between 0 and 1. To determine this score, a weighted sum of the attributes was used

In [ ]:
neighborhoods["PreScore"] = neighborhoods["QualityOfLife_Scaled"] * .6 + neighborhoods["Avg Rent_Scaled"] * .4
neighborhoods["LockdownScore"] = neighborhoods["Open_Scaled"] * .3 + (1-neighborhoods["CovidCasesPer100000_Scaled"]) * 0.3 + neighborhoods["Avg Rent_Scaled"] * .4

### Results <a class="anchor" id="results"></a>

The product of the above data wrangling and analysis is two scores for each neighborhood, one for before the pandemic and one during it.

In [ ]:
draw_map("Neighborhood Score Pre-Covid-19", "PreScore", "PreScore", True)

In [ ]:
draw_map("Neighborhood Score During Lockdown", "LockdownScore", "LockdownScore", True)

In [ ]:
neighborhoods['PreScore'].plot(kind="hist", title="Neighborhood Score Pre-Covid-19")

In [ ]:
neighborhoods['LockdownScore'].plot(kind="hist", title="Neighborhood Score During Lockdown")

It would appear from the map that South Dublin is the most desirable area both before and during the pandemic. While this may be true, we can conclude from both the map and the subsequent histograms that the spread of desirability is much broader during Lockdown. As anecdotally observed, the city centre is no longer the hub that it once was and the greater Dublin area proved more able to compete for residents.

In [ ]:
best_neighborhood_pre_covid = neighborhoods.loc[neighborhoods['PreScore'].idxmax()]
best_neighborhood_during_lockdown = neighborhoods.loc[neighborhoods['LockdownScore'].idxmax()]

In [ ]:
best_pre_covid_location = geolocator.reverse((best_neighborhood_pre_covid['Neighborhood Latitude'], best_neighborhood_pre_covid['Neighborhood Longitude']))
best_lockdown_location = geolocator.reverse((best_neighborhood_during_lockdown['Neighborhood Latitude'], best_neighborhood_during_lockdown['Neighborhood Longitude']))

print(f"The best neighborhood before the pandemic hit was {best_pre_covid_location.raw['address']['suburb']}")
print(f"The best neighborhood during lockdown was {best_lockdown_location.raw['address']['suburb']}")

### Discussion <a class="anchor" id="discussion"></a>

After applying a simple scoring function of a weighted sum of the properties of the neighborhoods, it was observed that the spread of desirability is significantly wider during Lockdown, when the suburbs can more easily compete with the city centre. This is in keeping with the anecdotal evidence that inspired this project, and may be an indicator of a less densely populated city centre in a post-pandemic Dublin.

Indeed, it has been noted (again anecdotally) that many people originally from outside of Dublin are moving out of the city entirely to return their home counties across Ireland. Here, rent is even cheaper and they may have family already rooted in the community. Future census information will hopefully yield data that will allow further investigation into the long term effects of the pandemic and a culture of working from home.

It is worth noting that the scoring system used for this project is subjective, and will vary depending on a person's tastes. As such, a next step for this project could be to determine a person's tastes, perhaps from a quiz, and use that information to give them a more personalised result. The possibilities are endless!

### Conclusion <a class="anchor" id="conclusion"></a>

The purpose of this project was to determine the optimal location in which to live in Dublin, taking into account the amenities available within a 5km radius, the average rent, and the latest Covid-19 incidence rate, specifically, during the Covid-19 pandemic.

We generated a 1km spaced grid of neighborhoods across Dublin, then for each neighbourhood acquired the nearby venues, average cost of renting, and 14-Day Covid-19 Incidence Rate.

After applying a simple scoring function to the neighborhoods, it was observed that the spread of desirability is significantly wider during Lockdown, when the suburbs can more easily compete with the city centre.